In [1]:
!pip install --upgrade pip
!pip install jax[tpu] -f https://storage.googleapis.com/jax-releases/libtpu_releases.html
# !pip install jax
!pip install jaxlib diffusers huggingface_hub flax transformers
!pip install orbax-checkpoint
!pip install -U huggingface_hub

Looking in links: https://storage.googleapis.com/jax-releases/libtpu_releases.html


In [2]:
from diffusers import FlaxUNet2DConditionModel
from IPython.display import clear_output

loaded_model = FlaxUNet2DConditionModel.from_pretrained('ekhalavyan/sdxl-unet')
clear_output(wait=False) # Clear the loading messages
unet_module = loaded_model[0] # Extract the Flax Module
# unet_variables = {'params': diff_unet[1]} # Extract the parameters

# print(unet_variables.keys())
unet_module

FlaxUNet2DConditionModel(
    # attributes
    sample_size = 128
    in_channels = 4
    out_channels = 4
    down_block_types = ['DownBlock2D', 'CrossAttnDownBlock2D', 'CrossAttnDownBlock2D']
    up_block_types = ['CrossAttnUpBlock2D', 'CrossAttnUpBlock2D', 'UpBlock2D']
    only_cross_attention = False
    block_out_channels = [320, 640, 1280]
    layers_per_block = 2
    attention_head_dim = [5, 10, 20]
    num_attention_heads = None
    cross_attention_dim = 2048
    dropout = 0.0
    use_linear_projection = True
    dtype = float32
    flip_sin_to_cos = True
    freq_shift = 0
    use_memory_efficient_attention = False
    split_head_dim = False
    transformer_layers_per_block = [1, 2, 10]
    addition_embed_type = 'text_time'
    addition_time_embed_dim = 256
    addition_embed_type_num_heads = 64
    projection_class_embeddings_input_dim = 2816
)

In [3]:
import jax
import numpy as np
import jax.numpy as jnp
import orbax.checkpoint

from pathlib import Path
from jax import pmap
from flax.jax_utils import replicate
from flax.training.common_utils import shard
from PIL import Image
from functools import partial
import matplotlib.pyplot as plt
from typing import Dict, List, Optional, Union
import requests
from io import BytesIO

from diffusers.utils import PIL_INTERPOLATION

from huggingface_hub import notebook_login
from diffusers import FlaxStableDiffusionPipeline
import transformers
import time
from diffusers.utils import make_image_grid
from huggingface_hub import hf_hub_download

In [4]:
from typing import Dict, List, Optional, Union
import requests
from io import BytesIO
from diffusers.utils import PIL_INTERPOLATION

In [5]:
sdxl_params = {}
dtype = jnp.bfloat16

In [6]:
sdxl_params['unet'] = {'params': jax.tree_util.tree_map(lambda x: x.astype(dtype), loaded_model[1])}

In [7]:
from transformers import CLIPTokenizer
tokenizer_1 = CLIPTokenizer.from_pretrained('openai/clip-vit-base-patch32')
tokenizer_2 = CLIPTokenizer.from_pretrained('openai/clip-vit-base-patch32')

In [8]:
from transformers import FlaxCLIPTextModel, FlaxCLIPTextModelWithProjection
text_encoder_1 = FlaxCLIPTextModel.from_pretrained('/kaggle/input/sdxl-text-encoder-1')
text_encoder_2 = FlaxCLIPTextModelWithProjection.from_pretrained('/kaggle/input/text-encoder-2')

In [9]:
sdxl_params['text_encoder_1'] = {'params': jax.tree_util.tree_map(lambda x: x.astype(dtype), text_encoder_1.params)}
sdxl_params['text_encoder_2'] = {'params': jax.tree_util.tree_map(lambda x: x.astype(dtype), text_encoder_2.params)}

In [10]:
from diffusers import FlaxAutoencoderKL
from IPython.display import clear_output

loaded_model = FlaxAutoencoderKL.from_pretrained('ekhalavyan/sdxl-vae')
clear_output(wait=False) # Clear the loading messages
vae_module = loaded_model[0] # Extract the Flax Module
# vae_variables = {'params': diff_vae[1]} # Extract the parameters

sdxl_params['vae'] = {'params': jax.tree_util.tree_map(lambda x: x.astype(dtype), loaded_model[1])}

# print(vae_variables.keys())
vae_module

FlaxAutoencoderKL(
    # attributes
    in_channels = 3
    out_channels = 3
    down_block_types = ['DownEncoderBlock2D', 'DownEncoderBlock2D', 'DownEncoderBlock2D', 'DownEncoderBlock2D']
    up_block_types = ['UpDecoderBlock2D', 'UpDecoderBlock2D', 'UpDecoderBlock2D', 'UpDecoderBlock2D']
    block_out_channels = [128, 256, 512, 512]
    layers_per_block = 2
    act_fn = 'silu'
    latent_channels = 4
    norm_num_groups = 32
    sample_size = 1024
    scaling_factor = 0.13025
    dtype = float32
)

In [11]:
from diffusers import FlaxEulerDiscreteScheduler
loaded_model = FlaxEulerDiscreteScheduler.from_pretrained('/kaggle/input/sdxl-scheduler/config.json')
scheduler_module = loaded_model[0]
scheduler_params = loaded_model[1]
sdxl_params['scheduler'] = {'params': loaded_model[1]}

In [12]:
loaded_model = 5

In [13]:
vae_scale_factor = 2 ** (len(vae_module.config.block_out_channels) - 1)
height = unet_module.config.sample_size * vae_scale_factor
width = unet_module.config.sample_size * vae_scale_factor

In [14]:
unet_module.config.sample_size * vae_scale_factor //2

512

In [15]:
guidance_scale = 5.0
num_steps = 25
default_seed = 33
strength = 0.8

In [16]:
def get_timestep_start(num_inference_steps, strength):
    # get the original timestep using init_timestep
    init_timestep = min(int(num_inference_steps * strength), num_inference_steps)

    t_start = max(num_inference_steps - init_timestep, 0)

    return t_start

In [17]:
start_timestep = get_timestep_start(num_steps, strength)

# latents_shape = (
#             1,
#             unet_module.config.in_channels,
#             height // vae_scale_factor,
#             width // vae_scale_factor
# )


In [18]:
# @jax.jit
@partial(
    jax.pmap,
    in_axes=(None, 0, 0, 0, 0, None, None, 0),
    static_broadcasted_argnums=(0, 5, 6),
)
def generate_img2img(
    sdxl_params,
    image,
    positive_input_ids,
    negative_input_ids=None,
    prng_seed=jax.random.PRNGKey(42),
    guidance_scale=5.0,
    num_inference_steps=50,
    noise: Optional[jnp.ndarray] = None,
):
    
    prompt_embeds = text_encoder_1(positive_input_ids,params=sdxl_params['text_encoder_1']['params'])[0]
    
    print("prompt_embeds", prompt_embeds.shape)
    
    batch_size = positive_input_ids.shape[0]

    max_length = positive_input_ids.shape[-1]

    if negative_input_ids is None:
        uncond_input = tokenizer_1([""] * batch_size, padding="max_length", max_length=max_length, return_tensors="np").input_ids
    else:
        uncond_input = neg_prompt_ids
    
    negative_prompt_embeds = text_encoder_1(uncond_input, params=sdxl_params['text_encoder_1']['params'])[0]
    context = jnp.concatenate([negative_prompt_embeds, prompt_embeds])

    latents_shape = (
            1,
            unet_module.config.in_channels,
            height // vae_scale_factor,
            width // vae_scale_factor
    )
    
    print("latents_shape: ", latents_shape)
    
    if noise is None:
        noise = jax.random.normal(prng_seed, shape=latents_shape, dtype=jnp.float32)
    else:
        if noise.shape != latents_shape:
            raise ValueError(f"Unexpected latents shape, got {noise.shape}, expected {latents_shape}")
            
    # Create init_latents
    init_latent_dist = vae_module.apply(sdxl_params['vae'], image, method=vae_module.encode).latent_dist
    init_latents = init_latent_dist.sample(key=prng_seed).transpose((0, 3, 1, 2))
    init_latents = vae_module.config.get("scaling_factor") * init_latents
    
    def loop_body(step, args):
        latents, scheduler_state = args
        # For classifier free guidance, we need to do two forward passes.
        # Here we concatenate the unconditional and text embeddings into a single batch
        # to avoid doing two forward passes
        latents_input = jnp.concatenate([latents] * 2)

        t = jnp.array(scheduler_state.timesteps, dtype=jnp.int32)[step]
        timestep = jnp.broadcast_to(t, latents_input.shape[0])

        latents_input = scheduler_module.scale_model_input(scheduler_state, latents_input, t)

        # predict the noise residual
        noise_pred = unet_module.apply(
            sdxl_params['unet'],
            jnp.array(latents_input),
            jnp.array(timestep, dtype=jnp.int32),
            encoder_hidden_states=prompt_embeds,
        ).sample
        # perform guidance
        noise_pred_uncond, noise_prediction_text = jnp.split(noise_pred, 2, axis=0)
        noise_pred = noise_pred_uncond + guidance_scale * (noise_prediction_text - noise_pred_uncond)

        # compute the previous noisy sample x_t -> x_t-1
        latents, scheduler_state = scheduler_module.step(scheduler_state, noise_pred, t, latents).to_tuple()
        return latents, scheduler_state
    
    scheduler_state = scheduler_module.set_timesteps(
        sdxl_params['scheduler']['params'], num_inference_steps=num_steps, shape=latents_shape
    )
    print(type(scheduler_state))

    latent_timestep = scheduler_state.timesteps[start_timestep : start_timestep + 1].repeat(1)

    print("latents shape: ", init_latents.shape, "noise shape: ", noise.shape, "latent time step:, ", type(latent_timestep), latent_timestep, start_timestep, 1)
    
    latents = scheduler_module.add_noise(sdxl_params['scheduler']['params'], init_latents, noise, latent_timestep)

    # scale the initial noise by the standard deviation required by the scheduler
    latents = latents * sdxl_params['scheduler']['params'].init_noise_sigma
    
    latents, _ = jax.lax.fori_loop(start_timestep, num_steps, loop_body, (latents, scheduler_state))
    latents = 1 / vae_module.config.get("scaling_factor") * latents
    
    image = vae_module.apply(sdxl_params['vae'], latents, method=vae_module.decode).sample
    image = (image / 2 + 0.5).clip(0, 1).transpose(0, 2, 3, 1)
    image = (image * 255).round().astype("uint8")
    return image    

In [19]:
# def tokenise_prompts(prompt):
#     inputs = []
#     for tokenizer in [tokenizer_1, tokenizer_2]:
#         text_inputs = tokenizer(
#             positive_prompt,
#             padding="max_length",
#             max_length=tokenizer.model_max_length,
#             truncation=True,
#             return_tensors="np",
#         )
#         inputs.append(text_inputs.input_ids)
#     return jnp.stack(inputs, axis=1)

def tokenise_prompts(prompt):
    text_inputs = tokenizer_1(
        positive_prompt,
        padding="max_length",
        max_length=tokenizer_1.model_max_length,
        truncation=True,
        return_tensors="np",
    )
    return text_inputs.input_ids

In [20]:
def preprocess(image, dtype):
    w, h = image.size
    w, h = (x - x % 32 for x in (w, h))  # resize to integer multiple of 32
    image = image.resize((w, h), resample=PIL_INTERPOLATION["lanczos"])
    image = jnp.array(image).astype(dtype) / 255.0
    image = image[None].transpose(0, 3, 1, 2)
    return 2.0 * image - 1.0

In [21]:
url = "https://www.baseballbible.net/wp-content/uploads/What-Is-a-Pull-Hitter-in-Baseball.jpg"
response = requests.get(url)
processed_images = preprocess(Image.open(BytesIO(response.content)).convert("RGB"), jnp.float32)

In [22]:
positive_prompt = '''Boy dressed in blue hitting with a baseball bat. Realistic. portrait, 80mm lens, shallow depth of field, 
close up, split lighting, cinematic'''
negative_prompt = None
prng_seed = replicate(jax.random.PRNGKey(default_seed))
positive_input_ids = replicate(tokenise_prompts(positive_prompt))
# sdxl_params = replicate(sdxl_params)
p_processed_image = replicate(processed_images)

#print("sdxl_params:", sdxl_params['text_encoder_1']['params']['text_model']['embeddings']['position_embedding']['embedding'].shape)

# prng_seed = jax.random.PRNGKey(default_seed)
# positive_input_ids = tokenise_prompts(positive_prompt)
print(positive_input_ids.shape)

print("Start Compiling")
start = time.time()
gen_image = generate_img2img(sdxl_params, p_processed_image, positive_input_ids, negative_prompt, prng_seed, guidance_scale, num_steps, noise = None)
print(f"Compiled in {time.time() - start}")
figsize=(10,10)
plt.figure(figsize=figsize)
plt.axis('off')
# plt.imshow(gen_image.reshape(gen_image.shape[1],gen_image.shape[2],gen_image.shape[3]))
plt.imshow(gen_image[0][0]) #.reshape(gen_image.shape[1],gen_image.shape[2],gen_image.shape[3]))

(8, 1, 77)
Start Compiling


ValueError: Non-hashable static arguments are not supported. An error occurred during a call to 'generate_img2img' while trying to hash an object of type <class 'dict'>, {'unet': {'params': {'add_embedding': {'linear_1': {'bias': Array([0.00854492, -0.0141602, -0.000663757, ..., -0.00848389, 0.00891113,
       0.010376], dtype=bfloat16), 'kernel': Array([[0.00637817, 0.0180664, -0.00836182, ..., -0.0145264, 0.00570679,
        -0.0027771],
       [0.0366211, 0.00367737, 0.00872803, ..., -0.0106812, 0.00361633,
        -0.00259399],
       [0.0134277, 0.00315857, 0.0018692, ..., 0.00100708, 0.0444336,
        -0.000385284],
       ...,
       [0.00337219, -0.0004673, -0.000143051, ..., 0.00427246,
        -0.00561523, -0.00570679],
       [-0.003479, 0.00138855, 0.00238037, ..., 0.000125885, -0.00125885,
        -0.000208855],
       [-0.00271606, 0.00069046, -0.00411987, ..., -0.00491333,
        -0.00087738, 0.00370789]], dtype=bfloat16)}, 'linear_2': {'bias': Array([-0.0114746, 0.005

In [ ]:
p_processed_image = replicate(processed_images) #print("sdxl_params:", sdxl_params['text_encoder_1']['params']['text_model']['embeddings']['position_embedding']['embedding'].shape)

In [ ]:
print("Start Compiling")
start = time.time()
gen_image = generate_img2img(sdxl_params, p_processed_image, positive_input_ids, negative_prompt, prng_seed, guidance_scale, num_steps, noise = None)
print(f"Compiled in {time.time() - start}")
figsize=(10,10)
plt.figure(figsize=figsize)
plt.axis('off')
# plt.imshow(gen_image.reshape(gen_image.shape[1],gen_image.shape[2],gen_image.shape[3]))
plt.imshow(gen_image[0][0]) #.reshape(gen_image.shape[1],gen_image.shape[2],gen_image.shape[3]))

In [ ]:
scheduler_module.add_noise()

In [ ]:
import jax
import jax.numpy as jnp
latents = jax.random.normal(jax.random.PRNGKey(42), shape=(1,4,128,256), dtype=jnp.float32)
image = vae_module.apply(vae_variables, latents, method=vae_module.decode).sample
image = (image / 2 + 0.5).clip(0, 1).transpose(0, 2, 3, 1)
image = (image[0] * 255).round().astype("uint8")
# test_image = (255*((test_image - test_image.min())/(test_image.max() - test_image.min()))).round().astype("uint8")
figsize=(10,10)
plt.figure(figsize=figsize)
plt.figure(figsize=figsize)
plt.axis('off')
plt.imshow(image) #.reshape(gen_image.shape[1],gen_image.shape[2],gen_image.shape[3]))

In [ ]:
from PIL import Image
pil_image = np.array(image)
pil_image = Image.fromarray(pil_image)
pil_image

In [ ]:
latents_shape_1 = (
            1,
            4,
            128,
            128
)


start_timestep = get_timestep_start(num_steps, strength)
scheduler_state = scheduler_module.set_timesteps(
       sdxl_params['scheduler']['params'], num_inference_steps=num_steps, shape=latents_shape_1
    )

latent_timestep = scheduler_state.timesteps[start_timestep : start_timestep + 1].repeat(1)
print(type(scheduler_state), "latent time step:, ", type(latent_timestep))

In [ ]:
print(positive_input_ids.shape[0], unet_module.config.in_channels,
                height // vae_scale_factor,
                width // vae_scale_factor)

In [ ]:
print(type(scheduler_state))

In [ ]:
scheduler_params

In [ ]:
type(sdxl_params['scheduler']['params']) == type(scheduler_params)